- Check the Binary  Feature Hypothesis.
    - After layernorm Features are either clearly present or clearly not present. E.g You take a feature like tile A4 is Mine and over many games you see a bimodal distribution over the length of the feature with little overlap
    - I can look at this. assuming that the residual stream is a linear combination of features. I want to find the factor of the current feature. But I don't have direct excess to that.
    - I could instead look at the cosine similiarity or dot product (Dot Product better)
    - Or I try to get all the features that are represented and estimate the coefficients (seems bad because I don't know all the features...)

In [4]:
from interpreting_neurons_utils import *

/hpi/fs00/home/jim.maar/miniconda3/envs/othello-env/lib/python3.11/site-packages/accelerate/utils/imports.py:274: UserWarning: `ACCELERATE_DISABLE_RICH` is deprecated and will be removed in v0.22.0 and deactivated by default. Please use `ACCELERATE_ENABLE_RICH` if you wish to use `rich`.
  warnings.warn(


In [5]:
focus_cache.keys()

dict_keys(['hook_embed', 'hook_pos_embed', 'blocks.0.hook_resid_pre', 'blocks.0.ln1.hook_scale', 'blocks.0.ln1.hook_normalized', 'blocks.0.attn.hook_q', 'blocks.0.attn.hook_k', 'blocks.0.attn.hook_v', 'blocks.0.attn.hook_attn_scores', 'blocks.0.attn.hook_pattern', 'blocks.0.attn.hook_z', 'blocks.0.hook_attn_out', 'blocks.0.hook_resid_mid', 'blocks.0.ln2.hook_scale', 'blocks.0.ln2.hook_normalized', 'blocks.0.mlp.hook_pre', 'blocks.0.mlp.hook_post', 'blocks.0.hook_mlp_out', 'blocks.0.hook_resid_post', 'blocks.1.hook_resid_pre', 'blocks.1.ln1.hook_scale', 'blocks.1.ln1.hook_normalized', 'blocks.1.attn.hook_q', 'blocks.1.attn.hook_k', 'blocks.1.attn.hook_v', 'blocks.1.attn.hook_attn_scores', 'blocks.1.attn.hook_pattern', 'blocks.1.attn.hook_z', 'blocks.1.hook_attn_out', 'blocks.1.hook_resid_mid', 'blocks.1.ln2.hook_scale', 'blocks.1.ln2.hook_normalized', 'blocks.1.mlp.hook_pre', 'blocks.1.mlp.hook_post', 'blocks.1.hook_mlp_out', 'blocks.1.hook_resid_post', 'blocks.2.hook_resid_pre', 'block

In [6]:
tile_label = "A3"
feature = "mine"
feature_int = get_direction_int(feature)
layer = 1
tile_tuple = label_to_tuple(tile_label)

resid_layer1 : Float[Tensor, "batch pos d_model"]= focus_cache[f"blocks.{layer}.ln2.hook_normalized"]
# print(resid_layer1.shape, resid_layer1.norm(dim=-1).shape)
# resid_layer1_normalized = einops.rearrange(resid_layer1, "batch pos d_model -> d_model batch pos") / resid_layer1.norm(dim=-1)
# resid_layer1_normalized = einops.rearrange(resid_layer1_normalized, "d_model batch pos -> batch pos d_model")
# resid_layer1 : Float[Tensor, "batch pos d_model"]= focus_cache["resid_pre", layer]
probe : Float[Tensor, "d_model rows cols options"] = get_probe(1, "linear", "mid")[0, :, :, :, :]
# probe_normalized = probe / probe.norm()

dot_product = einops.einsum(resid_layer1, probe, "batch pos d_model, d_model rows cols options -> batch pos rows cols options")
dot_product = dot_product.softmax(dim=-1)
dot_product = dot_product[..., *tile_tuple, feature_int]
dot_product = dot_product.flatten().cpu().numpy()

# dot_product = einops.einsum(resid_layer1_normalized, probe_normalized, "batch pos d_model, d_model -> batch pos").flatten().cpu().numpy()

# Create a histogram Plot using plotly express

fig = px.histogram(x=dot_product, nbins=50, range_x=[0, 1])
fig.update_layout(
    title=f"Dot product of the probe with the residual of the layer {layer} of the tile {tile_label}",
    xaxis_title="Dot product",
    yaxis_title="Frequency",
)
fig.show()

- Binary Feature Hypothesis    
    - For tile A4 and Mine the hypothesis seems true in layer 4 (After attention). Probably the accuracy is really high there.
    - For earlier Layers. the distribution is Bimodel but not as clear in the middle
    - Okay so using dot_product is a bit whack
    - Using softmax it's absulutely beautiful
    - Binary Feature Hypothesis true

- I want to get the average coefficent of a Feature if it is True.
    - But I don't know if this is possible
    - I could try to extract all the Features that seem true

1. For every Probe (specific to Tile etc.) compute best threshold using k-means (Or just use 0.5 ...)
2. Get the coefficients of the length of the features
    - Extract the Features present
    - automatically find the right coefficients to reconstruct the probe
        - I think this is quite hard
        - I probably need some base vector (e.g. mean residual stream to add to or learned vector)
        - look whats the name of this and search for libraries
3. Look if these have a small variance
4. If so, go over neurons. Look for what combination of features activates them. Extract rules
5. Categorize the rules and remove translation invariant rules etc.

In [7]:
device

device(type='cuda')

In [8]:
@dataclass
class CoefficientTrainingArgs():
    # Which layer, and which positions in a game sequence to probe
    layer: int = 1
    pos_start: int = 0
    pos_end: int = 59
    length: int = pos_end - pos_start
    max_epochs = 1

    num_games_train: int = 25000
    batch_size: int = 64

    lr: float = 1e-2
    betas: Tuple[float, float] = (0.9, 0.99)
    wd: float = 0.1

    run_number = 0
    # Misc.
    run_name: str = f"coefficients_{run_number}"
    full_run_name: str = f"coefficients_L{layer}_{run_number}"

    # wnadb
    wandb_project: str = f"Estimate Feature Coefficients"
    cache_position = "resid_post"

In [9]:
import pickle
import wandb

In [10]:
avg_resid : Float[Tensor, "d_model"] = einops.reduce(focus_cache[f"blocks.{1}.ln2.hook_normalized"], "batch pos d_model -> d_model", "mean")

In [11]:
index = 5

In [12]:
class LinearProbeTrainer:
    def __init__(self, model: HookedTransformer, args: CoefficientTrainingArgs, train_base_resid):
        self.model = model
        self.args = args
        avg_resid : Float[Tensor, "d_model"] = einops.reduce(focus_cache[f"blocks.{self.args.layer}.ln2.hook_normalized"], "batch pos d_model -> d_model", "mean")
        # self.base_resid = avg_resid.clone().to(device)
        # self.base_mean = self.base_resid.mean()
        # self.base_var = self.base_resid.var()
        self.train_base_resid = train_base_resid
        self.base_resid = t.zeros((512), requires_grad=False).to(device)
        self.coefficients = {
            "linear" : {
                "mine" : t.randn((8, 8), requires_grad=False).abs().to(device),
                "yours" :t.randn((8, 8), requires_grad=False).abs().to(device),
                "empty" :t.randn((8, 8), requires_grad=False).abs().to(device),
            },
            "flipped" : {
                "flipped" : t.randn((8, 8), requires_grad=False).abs().to(device),
                # "not_flipped" :t.randn((8, 8), requires_grad=False).abs().to(device),
            },
            "placed" : {
                "placed" :t.randn((8, 8), requires_grad=False).abs().to(device),
                # "not_placed" :t.randn((8, 8), requires_grad=False).abs().to(device),
            },
        }
        if self.train_base_resid:
            self.base_resid.requires_grad = True
        else:
            self.base_resid.requires_grad = False
        for probe_name in self.coefficients:
            for feature in self.coefficients[probe_name]:
                self.coefficients[probe_name][feature].requires_grad = True

    def training_step(self, indices: Int[Tensor, "game_idx"], train_or_val="train") -> t.Tensor:

        # Get the game sequences and convert them to state stacks
        games_int = board_seqs_int[indices.cpu()]
        games_str = board_seqs_string[indices.cpu()]
        # state_stack = t.stack([t.tensor(seq_to_state_stack(game_str.tolist())) for game_str in games_str])
        # state_stack = state_stack[:, self.args.pos_start: self.args.pos_end, :, :]
        batch_size = self.args.batch_size
        game_len = self.args.length
        # options = self.args.options
        d_model = 512

        # games_int = tensor of game sequences, each of length 60
        # This is the input to our model
        assert isinstance(games_int, Int[Tensor, f"batch={batch_size} full_game_len=60"])

        # SOLUTION
        with t.inference_mode():
            _, cache = model.run_with_cache(
                games_int[:, :-1].to(device),
                return_type=None,
                names_filter=lambda name: name == f"blocks.{self.args.layer}.ln2.hook_normalized"
            )
            resid = cache[f"blocks.{self.args.layer}.ln2.hook_normalized"][:, self.args.pos_start: self.args.pos_end]
        resid = resid.clone().detach().to(device)
        resid_approximation = t.zeros((batch_size, game_len, d_model)).to(device)
        resid_approximation = resid_approximation + self.base_resid
        for probe_name in self.coefficients:
            probe = probes[("mid", probe_name, self.args.layer)].clone().detach()[0]
            probe_result = einops.einsum(resid, probe, "batch pos d_model, d_model rows cols options -> batch pos rows cols options")
            probe_result : Float[Tensor, "batch pos rows cols"] = probe_result.argmax(dim=-1)
            for feature_str in self.coefficients[probe_name]:
                option = get_direction_int(feature_str)
                probe_result_bool : Float[Tensor, "batch pos rows cols"] = probe_result == option
                option_probe = probe[:, :, :, option] * self.coefficients[probe_name][feature_str]
                # option_probe = einops.rearrange(option_probe, "rows cols d_model -> d_model rows cols")
                option_probe = einops.repeat(option_probe, "d_model rows cols -> d_model batch pos rows cols", batch = batch_size, pos = game_len)
                option_probe = option_probe * probe_result_bool
                resid_approximation = resid_approximation + einops.reduce(option_probe, "d_model batch pos rows cols -> batch pos d_model", "sum")

        appr_mean = resid_approximation.mean()
        appr_var = resid_approximation.var()

        loss = t.nn.functional.mse_loss(resid, resid_approximation) # + 0.01 * ((appr_mean - self.base_mean)**2 + (appr_var - self.base_var)**2)
        
        if train_or_val == "train" and self.step % 10 == 0:
            wandb.log({f"{train_or_val}_loss": loss.item()}, step=self.step)
        self.step += 1

        return loss
        
    def save_coefficients(self, object, path):
        folder_path = "/".join(path.split("/")[:-1])
        if not os.path.exists(folder_path):
            os.makedirs(folder_path)
        with open(path, "wb") as f:
            pickle.dump(object, f)

    def shuffle_indices(self, start, num_games):
        '''
        Helper function
        '''
        n_indices = num_games - (num_games % self.args.batch_size)
        full_train_indices = t.randperm(num_games)[:n_indices] + start
        full_train_indices = einops.rearrange(full_train_indices, "(batch_idx game_idx) -> batch_idx game_idx", game_idx=self.args.batch_size)
        return full_train_indices
    
    def shuffle_training_indices(self):
        '''
        Returns the tensors you'll use to index into the training data.
        '''
        return self.shuffle_indices(0, self.args.num_games_train)

    def train(self):
        print(f"Training Probe: {self.args.full_run_name}")
        self.step = 0
        wandb.login()
        wandb.init(project=self.args.wandb_project, name=self.args.full_run_name, config=self.args)
        if self.train_base_resid:
            parameters = [{'params' : self.base_resid, 'lr' : self.args.lr * 0.1,  'weight_decay' : self.args.wd}]
        else:
            parameters = []
        for probe_name in self.coefficients:
            for feature in self.coefficients[probe_name]:
                parameters.append({'params' : self.coefficients[probe_name][feature]})

        optimizer = t.optim.AdamW(parameters, lr=self.args.lr, betas=self.args.betas, weight_decay=self.args.wd)

        for epoch in range(self.args.max_epochs):
            full_train_indices = self.shuffle_training_indices()
            progress_bar_train = tqdm(full_train_indices)
            for indices in progress_bar_train:
                loss = self.training_step(indices)
                loss.backward()
                optimizer.step()
                optimizer.zero_grad()
                progress_bar_train.set_description(f"Train_Loss = {loss:.4f}")

        wandb.finish()
        self.save_coefficients(self.base_resid, f"coefficients/base_resid_{self.args.run_number}_{index}.pth")
        self.save_coefficients(self.coefficients, f"coefficients/{self.args.full_run_name}.pth")
        print("Probe Trained and Saved")

In [13]:
'''# set torch to random seed and print the seed
t.manual_seed(42)

for i in range(0, 3):
    args = CoefficientTrainingArgs()
    args.run_number = i
    args.run_name = f"coefficients_{args.run_number}_{index}"
    args.full_run_name = f"coefficients_L{args.layer}_{args.run_number}_{index}"
    args.wandb_project = f"Estimate Feature Coefficients"
    trainer = LinearProbeTrainer(model, args, train_base_resid=False)
    trainer.train()
index += 1'''

'# set torch to random seed and print the seed\nt.manual_seed(42)\n\nfor i in range(0, 3):\n    args = CoefficientTrainingArgs()\n    args.run_number = i\n    args.run_name = f"coefficients_{args.run_number}_{index}"\n    args.full_run_name = f"coefficients_L{args.layer}_{args.run_number}_{index}"\n    args.wandb_project = f"Estimate Feature Coefficients"\n    trainer = LinearProbeTrainer(model, args, train_base_resid=False)\n    trainer.train()\nindex += 1'

In [14]:
how_many = 3

def cosine_similiarity(a, b):
    return t.nn.functional.cosine_similarity(a, b, dim=-1)

for i in range(how_many):
    base_resid_i = pickle.load(open(f"coefficients/base_resid_{i}_{index-1}.pth", "rb"))
    print(cosine_similiarity(base_resid_i, avg_resid))
    for j in range(how_many):
        base_resid_j = pickle.load(open(f"coefficients/base_resid_{j}_{index-1}.pth", "rb"))
        print(i, j, cosine_similiarity(base_resid_i, base_resid_j))


tensor(0.2823, device='cuda:0', grad_fn=<SumBackward1>)
0 0 tensor(1., device='cuda:0', grad_fn=<SumBackward1>)
0 1 tensor(0.6211, device='cuda:0', grad_fn=<SumBackward1>)
0 2 tensor(0.7730, device='cuda:0', grad_fn=<SumBackward1>)
tensor(0.3172, device='cuda:0', grad_fn=<SumBackward1>)
1 0 tensor(0.6211, device='cuda:0', grad_fn=<SumBackward1>)
1 1 tensor(1., device='cuda:0', grad_fn=<SumBackward1>)
1 2 tensor(0.6044, device='cuda:0', grad_fn=<SumBackward1>)
tensor(0.3308, device='cuda:0', grad_fn=<SumBackward1>)
2 0 tensor(0.7730, device='cuda:0', grad_fn=<SumBackward1>)
2 1 tensor(0.6044, device='cuda:0', grad_fn=<SumBackward1>)
2 2 tensor(1., device='cuda:0', grad_fn=<SumBackward1>)


In [15]:
tile_label = "E3"
probe_name = "flipped"
feature = "flipped"
feature_int = get_direction_int(feature)
layer = 1
tile_tuple = label_to_tuple(tile_label)

results = []
for i in range(how_many):
    coefficients = pickle.load(open(f"coefficients/coefficients_L{layer}_{i}_{index-1}.pth", "rb"))
    results += [coefficients[probe_name][feature][*tile_tuple].item()]
print(results)

fig = px.histogram(x=results, nbins=10, range_x=[-2.5, 2.5])
fig.update_layout(
    title=f"Coefficients of the \"{tile_label} is {feature}\" Feature for different taining runs (layer: {layer})",
    xaxis_title="Dot product",
    yaxis_title="Frequency",
)
fig.show()

[0.4610427916049957, 0.4458174705505371, 0.46241945028305054]


- We found a setup where all the coefficients converge
    - empty did not converge as well as the others
- Some very sparse features "A7" flipped became negative (I mean it makes sense it's probably not an actual feature the model is using)
- the Coefficients are dominated by the Placed Probe (which is like 7 times higher than the rest)
    - I think this is okay. It probably just contains a lot of information about everything else and it is sparse. And many of the other features e.g. empty are correlated with each other

- Next steps:
- Make histogram of Layer 1 Neuron activations
- Go over all Layer 1 Neurons.
- Extract all the Features with positive similiarity (above small threshold)
- Iterate over all subsets of features. Add all the feature directions with their corresponding coefficients together
- Look if Neuron Activates over threshold
- How do I test this?
    - I can calculate Precision and Recall (If Neuron Activates over threshholds. Do the Probes say it was because of one of the combinations and vice versa)

In [16]:
layer = 1

activations : Float[Tensor, "batch pos d_mlp"] = focus_cache["mlp_post", layer][:2]
activations = einops.rearrange(activations, "batch pos d_mlp -> (batch pos d_mlp)")
activations = activations[activations > 0]

In [17]:
fig = px.histogram(x=activations.to("cpu"), nbins=5000, range_x=[0, 1.5])
fig.update_layout(
    title=f"Activations of Neurons in Layer {layer} of the MLP",
    xaxis_title="Activations",
    yaxis_title="Count",
)
fig.show()

- The Histogram suggests setting the Threshhold for Neuron Activation to 0.0025 (Maybe even below that ...)

- New Plan:
    - Turn this into graph problem.
        - Find all the smallest subsets that activate the Neuron.
        - Make edge_weighs list by looking at the dot product to the input weights of the two added to gethter - the dot product with the input weights with just the larger one (Something like that (maybe just the first))
        - List of Groups (In the beginning each probe on theire own, with score (similiarity))
        - Pick best Group (priority queue) and Add the most promising candidate (highest weights)
        - If Score is High enough, add it to seperate group list, coninue
            - We continue with the same group but ban the tile that was enough, so that the tile doesen't come back later?
        - this is getting convoluted ...
        - first go easy: Set threshold higher and just stop when it is reached

- New New Plan:
- Create all the subsets where every node has positive weight with every other node
- Graph is directed and some how much similiarity gets better / worse
- also weird

- New New New Plan:
    - Just do Greedy ... (so that I get something)

In [28]:
layer = 1
neuron = 426

input_weights = get_w_in(model, layer, neuron)

In [29]:
coefficients = pickle.load(open(f"coefficients/coefficients_L{layer}_{0}_{5}.pth", "rb"))

In [34]:
def evaluate_group(group : List[Tuple[str, str]]):
    probes = [get_probe(layer, probe_name, "mid")[0, :, row, column, get_direction_int(direction_str)] for probe_name, direction_str, row, column in group]
    probe_coefficients = [coefficients[probe_name][direction_str][row, column] for probe_name, direction_str, row, column in group]
    probes = [probe * coefficient for probe, coefficient in zip(probes, probe_coefficients)]
    probes = t.stack(probes, dim=0).sum(dim=0)
    assert probes.shape == (512,)
    # print(probes.shape, input_weights.shape)
    return einops.einsum(probes, input_weights, "d_model, d_model -> ").item()

In [44]:
groups = []
for probe_name in coefficients:
    for direction_str in coefficients[probe_name]:
        if "not" in direction_str:
            continue
        for row in range(8):
            for column in range(8):
                groups.append([(probe_name, direction_str, row, column)])
scores = [(evaluate_group(group), i) for i, group in enumerate(groups)]
# sort group by score using lambda function
scores = sorted(scores, key=lambda x: x[0], reverse=True)
groups = [groups[i] for score, i in scores]
max_score = scores[0][0]
while True:
    best_group = groups[0]
    max_index = -1
    for i in range(1, len(groups)):
        group = groups[i]
        score = evaluate_group(best_group + group)
        if score > max_score:
            max_score = score
            max_index = i
            print(max_score)
    if score == 0:
        break
    print(f"add group: {groups[max_index]}")
    best_group += groups.pop(max_index)
best_group = groups[0]
print(best_group)

3.5500898361206055
add group: [('placed', 'placed', 6, 5)]
5.126775741577148
add group: [('placed', 'placed', 3, 6)]
6.53834867477417
add group: [('linear', 'empty', 3, 4)]
7.924553871154785
add group: [('placed', 'placed', 3, 5)]
9.276924133300781
add group: [('placed', 'placed', 1, 6)]
10.547647476196289
add group: [('placed', 'placed', 5, 5)]
11.80339241027832
add group: [('placed', 'placed', 6, 6)]
13.055432319641113
add group: [('placed', 'placed', 2, 2)]
14.296982765197754
add group: [('placed', 'placed', 7, 4)]
15.522758483886719
add group: [('placed', 'placed', 3, 2)]
16.732643127441406
add group: [('placed', 'placed', 0, 6)]
17.923049926757812
add group: [('placed', 'placed', 2, 0)]
19.109243392944336
add group: [('flipped', 'flipped', 0, 0)]
20.293968200683594
add group: [('placed', 'placed', 1, 2)]
21.47743797302246
add group: [('placed', 'placed', 7, 6)]
22.660648345947266
add group: [('placed', 'placed', 2, 1)]
23.8271484375
add group: [('placed', 'placed', 5, 4)]
24.98737

add group: [('placed', 'placed', 5, 6)]
28.435827255249023
add group: [('placed', 'placed', 2, 6)]
29.573657989501953
add group: [('placed', 'placed', 1, 1)]
30.692913055419922
add group: [('placed', 'placed', 5, 2)]
31.809425354003906
add group: [('placed', 'placed', 2, 5)]
32.91706848144531
add group: [('placed', 'placed', 3, 0)]
34.02387619018555
add group: [('placed', 'placed', 0, 3)]
35.12053680419922
add group: [('placed', 'placed', 4, 1)]
36.21387481689453
add group: [('placed', 'placed', 3, 1)]
37.30326843261719
add group: [('placed', 'placed', 5, 7)]
38.356666564941406
add group: [('placed', 'placed', 0, 5)]
39.409278869628906
add group: [('placed', 'placed', 6, 1)]
40.460052490234375
add group: [('placed', 'placed', 6, 2)]
41.508750915527344
add group: [('placed', 'placed', 7, 1)]
42.5483512878418
add group: [('placed', 'placed', 1, 5)]
43.58304977416992
add group: [('placed', 'placed', 0, 1)]
44.616153717041016
add group: [('placed', 'placed', 6, 4)]
45.64800262451172
add gr

KeyboardInterrupt: 

In [39]:
max(scores)

1.951573371887207

In [ ]:
from sklearn.cluster import KMeans

- For this I cannot use softmax, because then with flipped, everything would be activated

In [ ]:
layer = 1
neuron = 426
probe_name = "flipped"
direction_str = "flipped"
direction_int = get_direction_int(direction_str)
probe_module = "mid"
probe = get_probe(layer = layer, probe_type = probe_name, probe_module = probe_module).clone()
probe_normalized = probe / probe.norm(dim=1, keepdim=True)
neron_weights_all = []
for neuron in range(neuron, neuron+1):
    neuron_weights : Float[Tensor, "rows_cols"] = calculate_neuron_input_weights(model, probe_normalized, layer, neuron, direction_int).flatten()
    if direction_str == "empty":
        neuron_weights = t.cat([neuron_weights[0:27], neuron_weights[29:35], neuron_weights[37:]])
    neron_weights_all += [neuron_weights.cpu()]
neron_weights_all = t.stack(neron_weights_all)
neron_weights_all = neron_weights_all.flatten()#.unsqueeze(1)
# print(neron_weights_all.shape)
# k_means = KMeans(n_clusters=2, random_state=0).fit(neron_weights_all)

neuron_weights_all_for_k_means = neron_weights_all.unsqueeze(1)
# print(neron_weights_all.shape)
k_means = KMeans(n_clusters=2, random_state=0).fit(neuron_weights_all_for_k_means)
print(k_means.labels_)
print(k_means.cluster_centers_)
threshold = (k_means.cluster_centers_[0] + k_means.cluster_centers_[1]) / 2
print(threshold)

print(neron_weights_all.shape)

fig = px.histogram(x=neron_weights_all, nbins=30, range_x=[-1, 1])
fig.update_layout(
    title=f"Similiarity of Neuron weights to probe",
    xaxis_title="similiarity",
    yaxis_title="Count",
)
fig.show()

print("aahh")
print(k_means.cluster_centers_)
print(k_means.labels_[:100])

d_mlp = 512 * 4
for neuron in range(d_mlp):
    for probe_name in probe_directions:
        for direction_str, direction_int in probe_directions[probe_name].items():
            if "not" in direction_str:
                continue
            probe_module = "mid"
            probe = get_probe(layer = layer, probe_type = probe_name, probe_module = probe_module).clone()
            if probe.isnan().sum().item() > 0:
                print(f"Probe {probe_name} in is nan")
                continue
            probe_normalized = probe / probe.norm(dim=1, keepdim=True)
            neuron_weights : Float[Tensor, "rows cols"] = calculate_neuron_input_weights(model, probe_normalized, layer, neuron, direction_int)
            # Look what directions come into question
            # One threshold for all doesent work
            # Basically there should be outliers
            # this doesen't have to be very good ...
            # Use k-means?